In [1]:
import sys
import geopandas
import pandas as pd
import numpy as np
try:
    from osgeo import ogr, osr, gdal
except:
    sys.exit('ERROR: cannot find GDAL/OGR modules')

## load GIS vector data - waldorte

In [2]:
wo_geo = geopandas.read_file('/home/philipp/Data/edin_diss/GIS_test/joined.shp')

In [3]:
wo_geo.head()

OBJECTID  FORSTBETRI  REVIER_NR  ABTEILUNG UNTERABTEI  TEILFLAECH  \
0       1.0         171          1         -1          0           1   
1       2.0         171          1         -1          0           1   
2       3.0         171          1         -1          0           1   
3       4.0         171          1         -1          0           1   
4       5.0         171          1        506          3           1   

      FARBCODE                                  LINKID       ID  VERWALTUNG  \
0  00000000000  {7DDA8BDD-4E69-47D2-B7B5-D75FBCAAA0B2}  1450126         529   
1  00000000000  {2CAE2042-5D26-4B61-857B-A3643351503C}  1450044         529   
2  00000000000  {62D0D4D2-FFD0-45DD-8622-5B24494B182C}  1449991         529   
3  00000000000  {1AD6A0D3-C110-4E44-B7D8-DE5495E5C3EC}  1450382         529   
4  00000000003  {E77BB096-11C9-4939-9331-B4B305C4096A}  1450402         529   

                Erstellung               Datenaktua   SHAPE_Leng   SHAPE_Area  \
0  2020/11/20 09:37:18.000  2019/01/01 00:00:00.000   195.920109   1553.41910   
1  2020/11/20 09:37:18.000  2019/01/01 00:00:00.000  1125.586021  35217.65235   
2  2020/11/20 09:37:18.000  2019/01/01 00:00:00.000   946.503132  24184.69905   
3  2020/11/20 09:37:18.000  2019/01/01 00:00:00.000   319.914046   5266.03840   
4  2020/11/20 09:37:18.000  2019/01/01 00:00:00.000  2402.546849  11624.65550   

   FLUGJAHR                                           geometry  
0    2018.0  POLYGON ((616346.810 493670.595, 616342.890 49...  
1    2018.0  POLYGON ((615325.040 492902.555, 615263.980 49...  
2    2018.0  POLYGON ((608107.790 487993.105, 608108.120 48...  
3    2018.0  POLYGON ((614628.190 492540.735, 614612.100 49...  
4    2018.0  POLYGON ((617139.640 493799.045, 617151.260 49...

In [4]:
wo_geo.crs

{'init': 'epsg:31287'}

In [5]:
# filter abteilung -1
wo_geo = wo_geo.loc[wo_geo['ABTEILUNG'] != -1,:]

In [6]:
# create unique ID WO
wo_geo['WO'] = wo_geo['FORSTBETRI'].astype(str) + \
wo_geo['REVIER_NR'].astype(str).str.zfill(2) + \
wo_geo['ABTEILUNG'].astype(str).str.zfill(3) + \
wo_geo['UNTERABTEI'] + \
wo_geo['TEILFLAECH'].astype(str)

In [7]:
wo_geo['FLUGJAHR'] = wo_geo['FLUGJAHR'].fillna(0)
wo_geo['FLUGJAHR'] = wo_geo['FLUGJAHR'].astype(int)

In [8]:
wo_geo = wo_geo[wo_geo['FLUGJAHR'] != 0]

## load GIS vector data - orthophoto metadata

In [34]:
meta_geo = geopandas.read_file('/home/philipp/Data/edin_diss/GIS_meta/flugjahr.shp')

In [10]:
meta_geo = meta_geo[['FLUGJAHR', 'geometry']]

In [35]:
meta_geo.head()

FLUG_DAT  BOD_AUFL SPEKTRUM KAMERATYP BEMERKUNG MBL_NAME  DAT_LIEF_A  \
0  05.10.2018       0.2     RGBI      None      None  3621-47  23.05.2019   
1  08.08.2017       0.2     RGBI      None      None  4941-70  03.05.2018   
2  22.05.2016       0.2     RGBI      None      None  7827-24  19.06.2017   
3  26.08.2015       0.2     RGBI      None      None  1421-54  13.06.2016   
4  17.08.2013       0.0     RGBI      None      None  4318-06  27.05.2014   

   LFE_ID    LIEF_DAT BL_NAME  FLUGJAHR  \
0  1619.0  17.04.2019     TIR      2018   
1  1502.0  30.01.2018     OOE      2017   
2  1413.0  22.12.2016     BGL      2016   
3  1377.0  29.03.2016     TIR      2015   
4  1126.0  02.04.2014     KTN      2013   

                                            geometry  
0  MULTIPOLYGON Z (((376255.203 299731.999 0.000,...  
1  MULTIPOLYGON Z (((528150.720 311746.428 0.000,...  
2  MULTIPOLYGON Z (((493732.849 274749.378 0.000,...  
3  MULTIPOLYGON Z (((224688.559 321076.871 0.000,...  
4  POLYGON Z ((401249.684 315727.538 0.000, 40000...

### preform spatial join

In [ ]:
wo_geo = geopandas.sjoin(wo_geo, meta_geo, how='left', op='intersects')

In [ ]:
wo_geo.head()

## load SAP tax data

In [10]:
# get infromation about which Teiloperate were active in a giveb year

In [11]:
# set year
year = 2019

path_sap_info = '/home/philipp/Data/edin_diss/SAP_tax/edin_meta_data.xlsx'
sap_info = pd.read_excel(path_sap_info)

In [12]:
sap_info.head()

FB  FR  2007  2008  2009  2010  2011  2012  2013  2014  2015  2016  2017  \
0  171   1  1208  1208  1030  1030  1030  1030  1030  1030  1030  1030  1030   
1  171   2  1208  1208  1030  1030  1030  1030  1030  1030  1030  1030  1030   
2  171   3  1208  1208  1030  1030  1030  1030  1030  1030  1030  1030  1030   
3  171   4  1208  1208  1030  1030  1030  1030  1030  1030  1030  1030  1030   
4  171   5  1208  1208  1030  1030  1030  1030  1030  1030  1030  1030  1030   

   2018  2019  2020  2021  
0  1030  1030  1356  1356  
1  1030  1030  1356  1356  
2  1030  1030  1356  1356  
3  1030  1030  1356  1356  
4  1030  1030  1356  1356

In [13]:
# array with all TOs in a given year
tos = sap_info.loc[:,year].unique()

In [14]:
tos

array([1030, 1353, 1049, 1053, 1052, 1100, 1050, 1051, 1083, 1042, 1073,
       1092, 1311, 1342, 1151, 1194, 1086, 1043, 1144, 1197, 1055, 1303,
       1085, 1345, 1302, 1140, 1312, 1065, 1066, 1067, 1088, 1044, 1196,
       1313, 1343, 1354, 1093, 1045, 1081, 1082, 1341, 1355, 1156, 1250])

In [15]:
def get_data(tos):
    # set sap tax path directory
    path_sap_tax_dir = '/home/philipp/Data/edin_diss/SAP_tax'

    wo_sap_list = []

    for to in tos:
        # get fb
        fb = sap_info.loc[sap_info[year] == to, 'FB'].unique()[0]
        # create path to file
        path_sap_tax_file = path_sap_tax_dir + '/' + str(fb) + '/TO_' + str(to) + '.XLS'

        print(path_sap_tax_file)

        # read dat from file
        wo_sap_list.append(pd.read_csv(path_sap_tax_file, 
                                       sep='\t',
                                       encoding = "ISO-8859-1", 
                                       decimal=',', 
                                       error_bad_lines=False))
        # create unique ID WO
        #wo_sap['WO'] = wo_sap['Forstbetrieb'].astype(str) + \
        #wo_sap['Forstrevier'].astype(str) + \
        #wo_sap['Abteilung'].astype(str) + \
        #wo_sap['Unterabteil.'] + \
        #wo_sap['Teilfl.'].astype(str)

        #wo_sap_list.append(wo_sap)

    return pd.concat(wo_sap_list, ignore_index=True)

In [16]:
wo_sap = get_data(tos)

/home/philipp/Data/edin_diss/SAP_tax/171/TO_1030.XLS


/home/philipp/miniconda3/envs/geo/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3263: DtypeWarning: Columns (29,127,129,147,148,149) have mixed types.Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


/home/philipp/Data/edin_diss/SAP_tax/171/TO_1353.XLS


/home/philipp/miniconda3/envs/geo/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3263: DtypeWarning: Columns (29) have mixed types.Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


/home/philipp/Data/edin_diss/SAP_tax/171/TO_1049.XLS


...

/home/philipp/Data/edin_diss/SAP_tax/179/TO_1196.XLS
/home/philipp/Data/edin_diss/SAP_tax/179/TO_1313.XLS


/home/philipp/miniconda3/envs/geo/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3263: DtypeWarning: Columns (148) have mixed types.Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


/home/philipp/Data/edin_diss/SAP_tax/180/TO_1343.XLS
/home/philipp/Data/edin_diss/SAP_tax/180/TO_1354.XLS


/home/philipp/miniconda3/envs/geo/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3263: DtypeWarning: Columns (40,146,147,148,149) have mixed types.Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


/home/philipp/Data/edin_diss/SAP_tax/181/TO_1093.XLS
/home/philipp/Data/edin_diss/SAP_tax/181/TO_1045.XLS
/home/philipp/Data/edin_diss/SAP_tax/181/TO_1081.XLS
/home/philipp/Data/edin_diss/SAP_tax/181/TO_1082.XLS
/home/philipp/Data/edin_diss/SAP_tax/182/TO_1341.XLS
/home/philipp/Data/edin_diss/SAP_tax/182/TO_1355.XLS
/home/philipp/Data/edin_diss/SAP_tax/182/TO_1156.XLS
/home/philipp/Data/edin_diss/SAP_tax/182/TO_1250.XLS


In [17]:
wo_sap['Unterabteil.'].unique()

array(['B', 'C', 'A', 'D', 'G', 'F', 'E', 'L', 'H', 'N', 'I', 'K', '5',
       '3', '4', 'M', 'O', 'J', 'R', 'S', 'P', '9', '7', '8', '6', '1',
       'U', 'T', 'Z', 'V', 'W', 'Q', 'X', 'Y', '2'], dtype=object)

In [18]:
# create unique ID WO
wo_sap['WO'] = wo_sap['Forstbetrieb'].astype(str) + \
wo_sap['Forstrevier'].astype(str).str.zfill(2) + \
wo_sap['Abteilung'].astype(str).str.zfill(3) + \
wo_sap['Unterabteil.'] + \
wo_sap['Teilfl.'].astype(str)

In [19]:
wo_sap.head()

Merkmalausprägung  AuswKatTyp  Teiloperats-ID  Forstbetrieb  Debitor  \
0                  0         NaN            1030           171   220442   
1                  0         NaN            1030           171   220442   
2                  0         NaN            1030           171   220442   
3                  0         NaN            1030           171   220442   
4                  0         NaN            1030           171   220442   

  TO-Bezeichnung  Status Beg. Laufzeit Ende Laufzeit  Operat-ID  ...  \
0              1       2    01.01.2009    31.12.2019        111  ...   
1              1       2    01.01.2009    31.12.2019        111  ...   
2              1       2    01.01.2009    31.12.2019        111  ...   
3              1       2    01.01.2009    31.12.2019        111  ...   
4              1       2    01.01.2009    31.12.2019        111  ...   

                                              Zeile2  \
0  BE  Im N-TL gelichtet und winddurchrissen mit ...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                                NaN   

                                              Zeile3  \
0  diese hier älter (+5 J); ein Einzel-WW; im N-T...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                                NaN   

                           Zeile4           Zeile5 Zeile6  Zeile7  Zeile8  \
0  vergrast und leicht verkrautet  MA  BZ: 5LA 5BU    NaN     NaN     NaN   
1                             NaN              NaN    NaN     NaN     NaN   
2                             NaN              NaN    NaN     NaN     NaN   
3                             NaN              NaN    NaN     NaN     NaN   
4                             NaN              NaN    NaN     NaN     NaN   

   Bestockungsziel  Flächenanteil          WO  
0              NaN            0.0  17101648B1  
1              NaN            0.0  17101648B1  
2              NaN            0.0  17101648B1  
3              NaN            0.0  17101648B1  
4              NaN            0.0  17101648B1  

[5 rows x 153 columns]

In [20]:
# stoe

# filter data
wo_sap_stoe = wo_sap.loc[wo_sap['Best.-Schicht'] == 0, ['WO', 'Forstbetrieb', 'Forstrevier', 'Abteilung', 
                                                        'Unterabteil.', 'Teilfl.', 'Beg. Laufzeit', 'Umtriebszeit', 
                                                        'Nebengrund Art', 'Ertragssituation', 'Bewirtschaftungsform', 
                                                        'Schutzwaldkategorie', 'Seehöhe', 'Exposition', 'Neigung', 
                                                        'Standorteinheit', 'Vegetationstyp', 'Wuchsgebiet']]

wo_sap_stoe.head()

WO  Forstbetrieb  Forstrevier  Abteilung Unterabteil.  Teilfl.  \
0   17101648B1           171            1        648            B        1   
6   17101652C1           171            1        652            C        1   
12  17101736B4           171            1        736            B        4   
21  17101658A1           171            1        658            A        1   
27  17101506D1           171            1        506            D        1   

   Beg. Laufzeit  Umtriebszeit  Nebengrund Art Ertragssituation  \
0     01.01.2009           120             NaN                I   
6     01.01.2009           120             NaN                I   
12    01.01.2009           120             NaN                I   
21    01.01.2009           120             NaN                I   
27    01.01.2009           120             NaN                I   

   Bewirtschaftungsform Schutzwaldkategorie  Seehöhe Exposition  Neigung  \
0                     W                 NaN      400         SO       27   
6                     W                 NaN      400         SW       27   
12                    W                 NaN      300          S       18   
21                    W                 NaN      300         SW       18   
27                    W                 NaN      300         NO       27   

    Standorteinheit Vegetationstyp Wuchsgebiet  
0              87.0             BW         5.1  
6              87.0             WW         5.1  
12             87.0             WW         5.1  
21             87.0             WW         5.1  
27             88.0             WW         5.1

In [21]:
# wood volume

# filter data
wo_sap_v = wo_sap.loc[wo_sap['Best.-Schicht.1'] > 0, ['WO', 'Vorrat / ha', 'Laubholzvorrat / ha', 
                                                      'Nadelholzvorrat / ha', 'Vorrat am Ort', 
                                                      'Laubholzvorrat Ort', 'Nadelholzvorrat Ort',]]

# group by WO (ID) and sum all values
wo_sap_v = wo_sap_v.groupby(['WO']).sum().reset_index()

wo_sap_v.head()

WO  Vorrat / ha  Laubholzvorrat / ha  Nadelholzvorrat / ha  \
0  17101506A0        331.2               229.68                101.52   
1  17101506B1        236.7               208.18                 28.52   
2  17101506B2         13.0                13.00                  0.00   
3  17101506C1        175.0               175.00                  0.00   
4  17101506C2         89.0                72.90                 16.10   

   Vorrat am Ort  Laubholzvorrat Ort  Nadelholzvorrat Ort  
0        3083.47             2138.32               945.15  
1         295.88              260.23                35.65  
2           7.28                7.28                 0.00  
3         428.75              428.75                 0.00  
4         263.44              215.78                47.66

In [22]:
# wood cuts

# filter data
wo_sap_ma = wo_sap.loc[wo_sap['Nutzungsnummer'] > 0, ['WO', 'Maßnahmenart', 'Massnahmengruppe', 'Angriffsfläche', 
                                                      'Nutzung LH', 'Nutzung NH', 'Nutzungssumme', 'Nutzdringlichkeit', 
                                                      'Bewpfl.', 'Zeitpunkt', 'Rückungsart', 'Schlägerungsart']]

wo_sap_ma.head()

WO Maßnahmenart Massnahmengruppe  Angriffsfläche  Nutzung LH  \
5   17101648B1           RM               EN             4.0      1600.0   
10  17101652C1           DF               VN             3.0       100.0   
11  17101652C1           ZE               EN             0.0        30.0   
20  17101736B4           JP               WP             3.5         0.0   
26  17101658A1           DF               VN             4.0       200.0   

    Nutzung NH  Nutzungssumme  Nutzdringlichkeit  Bewpfl.  Zeitpunkt  \
5          0.0         1600.0                  2        3          2   
10         0.0          100.0                  2        1          2   
11        20.0           50.0                  3        1          2   
20         0.0            0.0                  1        1          1   
26         0.0          200.0                  2        1          2   

    Rückungsart  Schlägerungsart  
5          30.0              1.0  
10         30.0              1.0  
11         30.0              1.0  
20          NaN              NaN  
26         10.0              1.0

In [23]:
# filter just VN

In [24]:
wo_sap_maf = wo_sap_ma[wo_sap_ma['Massnahmengruppe'] == 'VN']
wo_sap_maf = wo_sap_maf[wo_sap_maf['Maßnahmenart'] != 'ZV']
wo_sap_maf = wo_sap_maf[wo_sap_maf['Maßnahmenart'] != 'UE']
wo_sap_maf = wo_sap_maf[wo_sap_maf['Maßnahmenart'] != 'LL']

In [25]:
wo_sap_maf['Maßnahmenart'].unique()

array(['DF', 'DE', 'ND'], dtype=object)

In [26]:
# get dublicated records
#wo_d = wo_sap_maf[wo_sap_maf.duplicated(subset = 'WO')]

In [27]:
# group by WO (ID) and sum all values
wo_sap_maf = wo_sap_maf.groupby(['WO']).sum().reset_index()

In [28]:
wo_sap_maf

WO  Angriffsfläche  Nutzung LH  Nutzung NH  Nutzungssumme  \
0      17101506A0             9.3       350.0       150.0          500.0   
1      17101506C1             0.6        30.0         0.0           30.0   
2      17101506C2             3.2       165.0         0.0          165.0   
3      17101506D2             2.8       120.0         0.0          120.0   
4      17101506G1             1.9        60.0        30.0           90.0   
...           ...             ...         ...         ...            ...   
37465  18209366L1             2.5         0.0       120.0          120.0   
37466  18209366L2             0.1         0.0        10.0           10.0   
37467  18209366M2             1.9         0.0        80.0           80.0   
37468  18209367H2             0.6         0.0        20.0           20.0   
37469  18209367H3             3.0         0.0       170.0          170.0   

       Nutzdringlichkeit  Bewpfl.  Zeitpunkt  Rückungsart  Schlägerungsart  
0                      2        1          2         30.0              1.0  
1                      1        1          2         10.0              1.0  
2                      3        2          4         45.0              5.0  
3                      2        1          2         35.0              4.0  
4                      1        1          2         35.0              4.0  
...                  ...      ...        ...          ...              ...  
37465                  1        1          1         35.0              4.0  
37466                  2        1          1         35.0              4.0  
37467                  1        1          1         35.0              4.0  
37468                  2        1          1         30.0              2.0  
37469                  1        1          1         30.0              2.0  

[37470 rows x 10 columns]

### merge all SAP data

In [29]:
# merge SAP stoe & SAP volume
wo_sap = pd.merge(wo_sap_stoe, wo_sap_v, how='left', on='WO', sort=False,
         suffixes=('_x', '_y'), copy=True, indicator=False,
         validate=None)

# merge
wo_sap = pd.merge(wo_sap, wo_sap_maf, how='left', on='WO', sort=False,
         suffixes=('_x', '_y'), copy=True, indicator=False,
         validate=None)

wo_sap.head()

WO  Forstbetrieb  Forstrevier  Abteilung Unterabteil.  Teilfl.  \
0  17101648B1           171            1        648            B        1   
1  17101652C1           171            1        652            C        1   
2  17101736B4           171            1        736            B        4   
3  17101658A1           171            1        658            A        1   
4  17101506D1           171            1        506            D        1   

  Beg. Laufzeit  Umtriebszeit  Nebengrund Art Ertragssituation  ...  \
0    01.01.2009           120             NaN                I  ...   
1    01.01.2009           120             NaN                I  ...   
2    01.01.2009           120             NaN                I  ...   
3    01.01.2009           120             NaN                I  ...   
4    01.01.2009           120             NaN                I  ...   

  Nadelholzvorrat Ort Angriffsfläche  Nutzung LH Nutzung NH  Nutzungssumme  \
0                0.00            NaN         NaN        NaN            NaN   
1              777.17            3.0       100.0        0.0          100.0   
2                0.00            NaN         NaN        NaN            NaN   
3                0.00            4.0       200.0        0.0          200.0   
4                0.00            NaN         NaN        NaN            NaN   

   Nutzdringlichkeit Bewpfl. Zeitpunkt  Rückungsart  Schlägerungsart  
0                NaN     NaN       NaN          NaN              NaN  
1                2.0     1.0       2.0         30.0              1.0  
2                NaN     NaN       NaN          NaN              NaN  
3                2.0     1.0       2.0         10.0              1.0  
4                NaN     NaN       NaN          NaN              NaN  

[5 rows x 33 columns]

In [30]:
wo_sap.to_csv('/home/philipp/Data/edin_diss/SAP.csv')

In [9]:
wo_sap = pd.read_csv('/home/philipp/Data/edin_diss/SAP.csv')

## load SAP nutz

In [10]:
def get_data_sap_nutz():
    # set sap tax path directory
    path_sap_nutz_dir = '/home/philipp/Data/edin_diss/SAP_nutz'

    sap_nutz_list = []

    for fb in range(171,183):
        # create path to file
        path_sap_file = path_sap_nutz_dir + '/FB' + str(fb) + '_2007_2019.xlsx'
        print(path_sap_file)
        # read dat from file
        sap_nutz_list.append(pd.read_excel(path_sap_file))

    return pd.concat(sap_nutz_list, ignore_index=True)

In [11]:
sap_nutz = get_data_sap_nutz()

/home/philipp/Data/edin_diss/SAP_nutz/FB171_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB172_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB173_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB174_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB175_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB176_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB177_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB178_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB179_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB180_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB181_2007_2019.xlsx
/home/philipp/Data/edin_diss/SAP_nutz/FB182_2007_2019.xlsx


In [12]:
# fill nan in 'Ergebnis'
sap_nutz = sap_nutz.fillna('Ergebnis')
# filter subtotals
sap_nutz = sap_nutz[sap_nutz['planmäßig'] != 'Ergebnis']
# reset index
sap_nutz = sap_nutz.reset_index(drop=True)

In [13]:
sap_nutz

Abmaßjahr           Waldort     Nutzungsart  planmäßig  Menge Efm
0           2007     #/171/1/710C1         Räumung  planmäßig     175.18
1           2007     #/171/1/740A0         Räumung  planmäßig     314.12
2           2007     #/171/3/146C1   Durchforstung  planmäßig      28.40
3           2007     #/171/4/421B0  Schäden andere   zufällig      25.20
4           2007     #/171/5/294G0    Schäden Wind   zufällig       8.39
...          ...               ...             ...        ...        ...
340306      2019  1355/182/5/297O5   Schäden Käfer   zufällig       1.74
340307      2019  1355/182/5/297O5    Schäden Wind   zufällig       5.22
340308      2019  1355/182/5/297O6   Schäden Käfer   zufällig       1.74
340309      2019  1355/182/5/297O7   Schäden Käfer   zufällig       1.16
340310      2019  1355/182/5/521G1    Schäden Wind   zufällig      15.00

[340311 rows x 5 columns]

In [14]:
# 
ids = sap_nutz['Waldort'].str.split('/')
# clear Waldort
sap_nutz['Waldort'] = ids.str[1] + ids.str[2].str.zfill(2) + ids.str[3].str.zfill(5)

In [15]:
sap_nutz['Waldort']

0         17101710C1
1         17101740A0
2         17103146C1
3         17104421B0
4         17105294G0
             ...    
340306    18205297O5
340307    18205297O5
340308    18205297O6
340309    18205297O7
340310    18205521G1
Name: Waldort, Length: 340311, dtype: object

In [16]:
# group by WO (ID) and sum all values
sap_nutz = sap_nutz.groupby(['Abmaßjahr','Waldort']).sum().reset_index()

In [17]:
sap_nutz.columns = ['cut_year', 'WO', 'cut_volume']
sap_nutz['cut_year'] = sap_nutz['cut_year'].astype(int)

In [18]:
sap_nutz

cut_year          WO  cut_volume
0          2007  17101506C1       7.800
1          2007  17101507B1       4.550
2          2007  17101508D1     736.480
3          2007  17101510A2       8.450
4          2007  17101510C1     477.180
...         ...         ...         ...
259961     2019  18209366H1      29.400
259962     2019  18209366H2       2.950
259963     2019  18209367F1      27.103
259964     2019  18209367K1      37.585
259965     2019  18209368A1     224.048

[259966 rows x 3 columns]

In [42]:
# merge
wo_sap = pd.merge(wo_sap, sap_nutz, how='left', on='WO', sort=False,
         suffixes=('_x', '_y'), copy=True, indicator=False,
         validate=None)

wo_sap.head()

WO  Forstbetrieb  Forstrevier  Abteilung Unterabteil.  Teilfl.  \
0  17101648B1           171            1        648            B        1   
1  17101648B1           171            1        648            B        1   
2  17101648B1           171            1        648            B        1   
3  17101648B1           171            1        648            B        1   
4  17101648B1           171            1        648            B        1   

  Beg. Laufzeit  Umtriebszeit  Nebengrund Art Ertragssituation  ...  \
0    01.01.2009           120             NaN                I  ...   
1    01.01.2009           120             NaN                I  ...   
2    01.01.2009           120             NaN                I  ...   
3    01.01.2009           120             NaN                I  ...   
4    01.01.2009           120             NaN                I  ...   

  Nutzung LH Nutzung NH  Nutzungssumme Nutzdringlichkeit  Bewpfl.  Zeitpunkt  \
0        NaN        NaN            NaN               NaN      NaN        NaN   
1        NaN        NaN            NaN               NaN      NaN        NaN   
2        NaN        NaN            NaN               NaN      NaN        NaN   
3        NaN        NaN            NaN               NaN      NaN        NaN   
4        NaN        NaN            NaN               NaN      NaN        NaN   

  Rückungsart Schlägerungsart  cut_year  cut_volume  
0         NaN             NaN      2007      209.23  
1         NaN             NaN      2008      631.13  
2         NaN             NaN      2009      230.76  
3         NaN             NaN      2015      413.43  
4         NaN             NaN      2016      342.05  

[5 rows x 35 columns]

In [19]:
wo_sap['FE_year'] = wo_sap['Beg. Laufzeit'].str[-4:].astype(int)

In [20]:
wo_sap

Unnamed: 0          WO  Forstbetrieb  Forstrevier  Abteilung  \
0                0  17101648B1           171            1        648   
1                1  17101652C1           171            1        652   
2                2  17101736B4           171            1        736   
3                3  17101658A1           171            1        658   
4                4  17101506D1           171            1        506   
...            ...         ...           ...          ...        ...   
231153      231153  18208062B5           182            8         62   
231154      231154  18208022A3           182            8         22   
231155      231155  18208020B2           182            8         20   
231156      231156  18209324C4           182            9        324   
231157      231157  18209323P4           182            9        323   

       Unterabteil.  Teilfl. Beg. Laufzeit  Umtriebszeit  Nebengrund Art  ...  \
0                 B        1    01.01.2009           120             NaN  ...   
1                 C        1    01.01.2009           120             NaN  ...   
2                 B        4    01.01.2009           120             NaN  ...   
3                 A        1    01.01.2009           120             NaN  ...   
4                 D        1    01.01.2009           120             NaN  ...   
...             ...      ...           ...           ...             ...  ...   
231153            B        5    01.01.2016           140             NaN  ...   
231154            A        3    01.01.2016           140             NaN  ...   
231155            B        2    01.01.2016           140             NaN  ...   
231156            C        4    01.01.2016           140             NaN  ...   
231157            P        4    01.01.2016           140             NaN  ...   

       Angriffsfläche Nutzung LH Nutzung NH  Nutzungssumme Nutzdringlichkeit  \
0                 NaN        NaN        NaN            NaN               NaN   
1                 3.0      100.0        0.0          100.0               2.0   
2                 NaN        NaN        NaN            NaN               NaN   
3                 4.0      200.0        0.0          200.0               2.0   
4                 NaN        NaN        NaN            NaN               NaN   
...               ...        ...        ...            ...               ...   
231153            NaN        NaN        NaN            NaN               NaN   
231154            4.0        0.0      150.0          150.0               1.0   
231155            NaN        NaN        NaN            NaN               NaN   
231156            NaN        NaN        NaN            NaN               NaN   
231157            1.2        0.0       80.0           80.0               1.0   

        Bewpfl.  Zeitpunkt Rückungsart  Schlägerungsart  FE_year  
0           NaN        NaN         NaN              NaN     2009  
1           1.0        2.0        30.0              1.0     2009  
2           NaN        NaN         NaN              NaN     2009  
3           1.0        2.0        10.0              1.0     2009  
4           NaN        NaN         NaN              NaN     2009  
...         ...        ...         ...              ...      ...  
231153      NaN        NaN         NaN              NaN     2016  
231154      1.0        2.0        10.0              1.0     2016  
231155      NaN        NaN         NaN              NaN     2016  
231156      NaN        NaN         NaN              NaN     2016  
231157      1.0        1.0        30.0              5.0     2016  

[231158 rows x 35 columns]

In [21]:
wo = wo_geo.merge(wo_sap, on='WO')

In [22]:
wo.columns

Index(['OBJECTID', 'FORSTBETRI', 'REVIER_NR', 'ABTEILUNG', 'UNTERABTEI',
       'TEILFLAECH', 'FARBCODE', 'LINKID', 'ID', 'VERWALTUNG', 'Erstellung',
       'Datenaktua', 'SHAPE_Leng', 'SHAPE_Area', 'FLUGJAHR', 'geometry', 'WO',
       'Unnamed: 0', 'Forstbetrieb', 'Forstrevier', 'Abteilung',
       'Unterabteil.', 'Teilfl.', 'Beg. Laufzeit', 'Umtriebszeit',
       'Nebengrund Art', 'Ertragssituation', 'Bewirtschaftungsform',
       'Schutzwaldkategorie', 'Seehöhe', 'Exposition', 'Neigung',
       'Standorteinheit', 'Vegetationstyp', 'Wuchsgebiet', 'Vorrat / ha',
       'Laubholzvorrat / ha', 'Nadelholzvorrat / ha', 'Vorrat am Ort',
       'Laubholzvorrat Ort', 'Nadelholzvorrat Ort', 'Angriffsfläche',
       'Nutzung LH', 'Nutzung NH', 'Nutzungssumme', 'Nutzdringlichkeit',
       'Bewpfl.', 'Zeitpunkt', 'Rückungsart', 'Schlägerungsart', 'FE_year'],
      dtype='object')

In [23]:
wo[['FE_year', 'FLUGJAHR']]

FE_year  FLUGJAHR
0          2009      2018
1          2009      2018
2          2009      2018
3          2009      2018
4          2009      2018
...         ...       ...
370528     2015      2013
370529     2015      2013
370530     2015      2013
370531     2015      2013
370532     2017      2013

[370533 rows x 2 columns]

In [38]:
temp = wo.loc[wo['WO']=='17101506C1',['FE_year', 'FLUGJAHR']]

In [64]:
flug_year = int(temp.iloc[0,1])

In [65]:
flug_year

2018

In [101]:
wo_data = wo.copy()

In [102]:
wo_data

OBJECTID  FORSTBETRI  REVIER_NR  ABTEILUNG UNTERABTEI  TEILFLAECH  \
0            5.0         171          1        506          3           1   
1            6.0         171          1        506          9           2   
2            7.0         171          1        506          A           0   
3            8.0         171          1        506          B           1   
4            9.0         171          1        506          B           1   
...          ...         ...        ...        ...        ...         ...   
370528  191316.0         177          2        150          K           3   
370529  191317.0         177          2        150          K           4   
370530  191318.0         177          2        150          M           0   
370531  191319.0         177          2        150          M           0   
370532  203989.0         177          7         35          7           4   

           FARBCODE                                  LINKID       ID  \
0       00000000003  {E77BB096-11C9-4939-9331-B4B305C4096A}  1450402   
1       00000000009  {99BC61C0-CE00-48BB-9140-A0C6D3EB5EA1}  1450449   
2       14000000000  {D5C7009D-5ED1-44F3-9A10-2EA9AC58094E}  1450404   
3       28000400000  {E3993FFC-AC51-468D-9B23-A733AF0079C9}  1450511   
4       28000400000  {EA311B6D-6915-49CE-B17A-43499CA9077D}  1450405   
...             ...                                     ...      ...   
370528  11000000000  {8AFA0E7C-F3B3-4A29-9D07-0256BEF8009B}  1618552   
370529  11000000000  {E4CF5974-C830-4C9A-8314-AE15DA5A8F49}  1618557   
370530  48010030300  {C0791AFB-6FD1-419F-B5C9-B937A816768C}  1618564   
370531  48010030300  {AF31F1D8-4666-4DC0-958B-86E49406698F}  1618574   
370532  00000000007  {926B0E5E-9DD9-4323-9DAA-A82A0912711C}  1696242   

        VERWALTUNG  ... Angriffsfläche Nutzung LH  Nutzung NH  Nutzungssumme  \
0              529  ...            NaN        NaN         NaN            NaN   
1              529  ...            NaN        NaN         NaN            NaN   
2              529  ...            9.3      350.0       150.0          500.0   
3              529  ...            NaN        NaN         NaN            NaN   
4              529  ...            NaN        NaN         NaN            NaN   
...            ...  ...            ...        ...         ...            ...   
370528         586  ...            NaN        NaN         NaN            NaN   
370529         586  ...            NaN        NaN         NaN            NaN   
370530         586  ...            NaN        NaN         NaN            NaN   
370531         586  ...            NaN        NaN         NaN            NaN   
370532         610  ...            NaN        NaN         NaN            NaN   

        Nutzdringlichkeit Bewpfl. Zeitpunkt  Rückungsart  Schlägerungsart  \
0                     NaN     NaN       NaN          NaN              NaN   
1                     NaN     NaN       NaN          NaN              NaN   
2                     2.0     1.0       2.0         30.0              1.0   
3                     NaN     NaN       NaN          NaN              NaN   
4                     NaN     NaN       NaN          NaN              NaN   
...                   ...     ...       ...          ...              ...   
370528                NaN     NaN       NaN          NaN              NaN   
370529                NaN     NaN       NaN          NaN              NaN   
370530                NaN     NaN       NaN          NaN              NaN   
370531                NaN     NaN       NaN          NaN              NaN   
370532                NaN     NaN       NaN          NaN              NaN   

        FE_year  
0          2009  
1          2009  
2          2009  
3          2009  
4          2009  
...         ...  
370528     2015  
370529     2015  
370530     2015  
370531     2015  
370532     2017  

[370533 rows x 51 columns]

In [103]:
np_nutz = sap_nutz.values

In [140]:
np_wo = wo_data[['WO','FE_year', 'FLUGJAHR', 'SHAPE_Area', 'OBJECTID']].values

In [141]:
np_wo

array([['1710150631', 2009, 2018, 11624.6554996582, 5.0],
       ['1710150692', 2009, 2018, 3111.4353746856077, 6.0],
       ['17101506A0', 2009, 2018, 93101.34739962808, 7.0],
       ...,
       ['17702150M0', 2015, 2013, 8861.101586502582, 191318.0],
       ['17702150M0', 2015, 2013, 15139.0446723904, 191319.0],
       ['1770703574', 2017, 2013, 10201.78817499057, 203989.0]],
      dtype=object)

In [104]:
np_nutz

array([[2007, '17101506C1', 7.8],
       [2007, '17101507B1', 4.55],
       [2007, '17101508D1', 736.48],
       ...,
       [2019, '18209367F1', 27.103],
       [2019, '18209367K1', 37.585],
       [2019, '18209368A1', 224.048]], dtype=object)

In [ ]:
for i in range(np_wo.shape[0]):   
    # mask WO
    mask_wo = np_nutz[:,1] == np_wo[i, 0]
    # mask earlier than fe year
    mask_fe = np_nutz[:,0] >= np_wo[i, 1]
    # mask later than photo year
    mask_photo = np_nutz[:,0] < np_wo[i, 2]
    # create final mask
    mask = mask_wo * mask_fe * mask_photo
    # filter array with mask
    cut = np_nutz[mask,-1].sum()
    np_wo[i, -1] = cut

In [131]:
mask1 = np_nutz[:,1] == '17101506C1'

In [132]:
mask2 = np_nutz[:,0] >= 2009

In [133]:
mask3 = np_nutz[:,0] < 2018

In [134]:
mask = mask1*mask2*mask3

In [135]:
mask

array([False, False, False, ..., False, False, False])

In [139]:
np_nutz[mask,-1].sum()

24.05

In [87]:
wo_data

OBJECTID  FORSTBETRI  REVIER_NR  ABTEILUNG UNTERABTEI  TEILFLAECH  \
0            5.0         171          1        506          3           1   
1            6.0         171          1        506          9           2   
2            7.0         171          1        506          A           0   
3            8.0         171          1        506          B           1   
4            9.0         171          1        506          B           1   
...          ...         ...        ...        ...        ...         ...   
370528  191316.0         177          2        150          K           3   
370529  191317.0         177          2        150          K           4   
370530  191318.0         177          2        150          M           0   
370531  191319.0         177          2        150          M           0   
370532  203989.0         177          7         35          7           4   

           FARBCODE                                  LINKID       ID  \
0                 A  {E77BB096-11C9-4939-9331-B4B305C4096A}  1450402   
1                 A  {99BC61C0-CE00-48BB-9140-A0C6D3EB5EA1}  1450449   
2                 A  {D5C7009D-5ED1-44F3-9A10-2EA9AC58094E}  1450404   
3                 A  {E3993FFC-AC51-468D-9B23-A733AF0079C9}  1450511   
4                 A  {EA311B6D-6915-49CE-B17A-43499CA9077D}  1450405   
...             ...                                     ...      ...   
370528  11000000000  {8AFA0E7C-F3B3-4A29-9D07-0256BEF8009B}  1618552   
370529  11000000000  {E4CF5974-C830-4C9A-8314-AE15DA5A8F49}  1618557   
370530  48010030300  {C0791AFB-6FD1-419F-B5C9-B937A816768C}  1618564   
370531  48010030300  {AF31F1D8-4666-4DC0-958B-86E49406698F}  1618574   
370532  00000000007  {926B0E5E-9DD9-4323-9DAA-A82A0912711C}  1696242   

        VERWALTUNG  ... Angriffsfläche Nutzung LH  Nutzung NH  Nutzungssumme  \
0              529  ...            NaN        NaN         NaN            NaN   
1              529  ...            NaN        NaN         NaN            NaN   
2              529  ...            9.3      350.0       150.0          500.0   
3              529  ...            NaN        NaN         NaN            NaN   
4              529  ...            NaN        NaN         NaN            NaN   
...            ...  ...            ...        ...         ...            ...   
370528         586  ...            NaN        NaN         NaN            NaN   
370529         586  ...            NaN        NaN         NaN            NaN   
370530         586  ...            NaN        NaN         NaN            NaN   
370531         586  ...            NaN        NaN         NaN            NaN   
370532         610  ...            NaN        NaN         NaN            NaN   

        Nutzdringlichkeit Bewpfl. Zeitpunkt  Rückungsart  Schlägerungsart  \
0                     NaN     NaN       NaN          NaN              NaN   
1                     NaN     NaN       NaN          NaN              NaN   
2                     2.0     1.0       2.0         30.0              1.0   
3                     NaN     NaN       NaN          NaN              NaN   
4                     NaN     NaN       NaN          NaN              NaN   
...                   ...     ...       ...          ...              ...   
370528                NaN     NaN       NaN          NaN              NaN   
370529                NaN     NaN       NaN          NaN              NaN   
370530                NaN     NaN       NaN          NaN              NaN   
370531                NaN     NaN       NaN          NaN              NaN   
370532                NaN     NaN       NaN          NaN              NaN   

        FE_year  
0          2009  
1          2009  
2          2009  
3          2009  
4          2009  
...         ...  
370528     2015  
370529     2015  
370530     2015  
370531     2015  
370532     2017  

[370533 rows x 51 columns]

In [32]:
%%time
for wo_id in wo['WO'].unique():
    print(wo_id)
    temp = wo.loc[wo['WO']==wo_id,['FE_year', 'FLUGJAHR']]
    fe_year = int(temp.iloc[0,0])
    flug_year = int(temp.iloc[0,1])
    
    sap_nutz[(sap_nutz['WO']=='17101506C1') & (sap_nutz['cut_year'] >= fe_year) & (sap_nutz['cut_year'] < flug_year)]

1710150631
1710150692
17101506A0
17101506B1
17101506B2
17101506C1
17101506C2
17101506D1
17101506D2
17101506D3
17101506D4
17101506F1
17101506F2
17101506G1
17101506G2
1710150731
1710150771
1710150772
1710150791
17101507A0
17101507B1
17101507B3
17101507B4
17101507C1
17101507C2
1710150831
17101508A1
17101508A2
17101508A3
17101508A4
17101508A5
17101508B2
17101508B4
17101508C1
17101508C2
17101508D2
17101508D3
17101508D4
17101508E0
1710150931
1710150971
17101509A2
17101509B1
17101509B2
17101509B3
17101509B4
1710151031
1710151071
17101510A1
17101510A2
17101510B1
17101510D0
1710151131
17101511A1
17101511A2
17101511B0
17101511C0
17101511D0
17101511E0
17101511F3
17101511G2
17101511H1
17101511H2
17101511H3
17101512A1
17101512A2
17101512B1
17101512B2
17101512C1
17101512F1
17101512F3
1710151331
17101513A1
17101513A2
17101513B2
17101513C0
17101514A1
17101514A2
17101514A3
17101514A4
17101514B0
17101514D1
17101514D2
17101514E0
17101514F3
17101514G1
17101514G2
17101515A1
17101515A2
17101515A3
17101515B0

17109083A5
17109083A6
17109083B1
17109083B4
17109083B5
1710908432
1710908531
17109086A2
17109086A3
1710908745
17109087A4
17109087B4
17109087B5
17109087F1
17109089B1
17109089B2
1710909241
17109092A1
1710909331
1710909341
17109093D0
1710917531
17109175B0
17109175C1
17109175C2
17109175C3
17109175C4
17109175D0
17109175E0
1710917631
1710917641
17109180G2
1710918331
1710918341
17109183B0
17109183C0
17109183D1
17109183D2
17109183E0
17109183F0
1710936031
17109360A1
17109360A2
17109360C1
17109360C2
1710936633
17109366A3
17109366A5
17109366B4
17109366E0
17109366F1
1710936731
1710936751
17109367B2
17109367E1
17109367E3
17109367F0
1710936942
17109369A4
17109369B3
17109369C1
17109369C2
17109370B3
1710937132
17109371A1
17109371A4
17109371B1
17109371C0
1710937341
17109374G0
17109375B2
17109375B3
17109375C1
17109375I0
17109376B0
17109377G0
17109378B2
17109381E2
1710938241
17109382B1
17109382B2
17109382C0
17109382D1
17109382D2
17109382F0
17109382G1
17109382G2
17109382I1
17109382I3
17109382I4
1710901842

17102635F4
1710263631
1710263641
1710263642
17102636A1
17102636A2
17102636A3
17102636A4
17102636A5
17102636B1
17102636B2
17102636C0
17102636D0
17102636E1
17102636E2
17102636E3
17102636F0
17102636G0
17102636H1
17102636H2
1710263731
1710263741
17102637A0
17102637B0
17102637C0
17102637D1
17102637D2
17102637D3
1710263831
1710263841
1710263842
1710263851
17102638A1
17102638A2
17102638A3
17102638A4
17102638B1
17102638B2
17102638C0
17102638D1
17102638D2
17102638D3
17102638E1
17102638E2
17102638E3
1710263931
1710263941
1710263942
17102639A1
17102639A2
17102639B1
17102639B2
17102639C1
17102639C2
17102639C3
17102639C4
17102639C5
17102639D1
17102639D2
17102639D3
17102639D4
17102639E0
1710264031
1710264051
1710264091
17102640A1
17102640A2
17102640A3
17102640A4
17102640B1
17102640B2
17102640C0
1710264131
1710264132
1710264141
1710264151
1710264171
1710264191
17102641A1
17102641A2
17102641A3
17102641B1
17102641B2
17102641B3
17102641B4
17102641C0
17102641D0
1710264231
1710264232
1710264233
1710264251

17104059H3
17104059I0
17104059J0
1710406031
1710406032
17104060A1
17104060A2
17104060A3
17104060A4
17104060B0
17104060C1
17104060C2
1710406131
17104061A1
17104061A2
17104061A3
17104061A4
17104061B0
17104061C1
17104061C2
17104061C3
17104061C4
17104061D0
17104061E1
17104061E2
17104061E3
1710406231
17104062A0
17104062B1
17104062B2
17104062B3
17104062B4
1710406331
1710406341
1710406342
1710406361
17104063A1
17104063A2
17104063B1
17104063B2
17104063C1
17104063C2
17104063C3
17104063C4
17104063C5
17104063C6
17104063C7
17104063D1
17104063D2
17104063E0
1710406431
17104064A0
17104064B0
17104064C0
17104064D0
17104064E0
17104064F0
17104064G0
1710406531
1710406551
1710406591
17104065A1
17104065A2
17104065A3
17104065A4
17104065B1
17104065B2
17104065B3
17104065C0
17104065D0
17104065E0
17104065F0
17104065G1
17104065G2
17104065G3
1710406631
1710406641
1710406642
1710406643
1710406644
17104066A1
17104066A2
17104066D1
17104066D2
17104066E0
17104066F1
17104066F2
1710406731
1710406741
1710406742
1710406743

17105118K0
17105118L1
17105118L2
17105118L3
1710511931
1710511941
1710511942
1710511951
1710511952
1710511991
17105119A1
17105119A2
17105119A3
17105119B1
17105119B2
17105119D0
17105119E0
17105119F1
17105119F2
17105119F3
17105119G0
17105119H0
1710512031
1710512032
1710512033
1710512041
1710512042
1710512043
1710512051
1710512052
1710512053
17105120A1
17105120A2
17105120B0
17105120C1
17105120C2
17105120C3
17105120C4
17105120D0
17105120E0
17105120F1
17105120F2
17105120G0
17105120H0
17105120I0
17105120K0
1710512131
1710512141
1710512142
1710512143
17105121A0
17105121B0
17105121C1
17105121C2
17105121D0
17105121E0
17105121F0
17105121G0
1710512231
1710512241
1710512242
17105122A0
17105122B1
17105122B2
17105122B3
17105122C1
17105122C2
17105122C3
17105122C4
1710512331
1710512341
1710512342
1710512351
17105123A1
17105123A2
17105123B0
17105123C0
17105123D0
17105123E0
17105123F0
17105123G0
17105123H1
17105123H2
1710512431
1710512432
17105124A0
17105124B0
17105124C0
17105124D1
17105124D2
17105124E1

...

18204164E2
18204164E3
18204164E4
18204164E5
18204164F1
18204164F2
18204164F3
18204164F4
18204164F5
18204164F6
18204164F7
18204164H1
18204164H2
18204164H3
18204164H4
18204164H5
18204164I1
18204164I2
18204164I3
18204164I4
18204164I5
18204164I6
18204164K0
18204164L1
18204164L2
18204164L3
18204164L4
18204164L5
18204164L6
18204164M0
18204164N1
18204164N2
18204164O1
18204164O2
18204164O3
18204164O4
18204164P1
18204164P2
18204164Q0
1820416511
1820416531
1820416532
1820416533
1820416542
1820416551
1820416552
1820416581
1820416582
1820416583
1820416584
18204165A1
18204165A2
18204165B1
18204165B2
18204165B3
18204165B4
18204165B5
18204165C1
18204165C2
18204165C3
18204165C4
18204165C5
18204165C6
18204165C7
18204165C8
18204165D1
18204165D2
18204165D3
18204165E1
18204165E2
18204165E3
18204165E4
18204165E5
18204165E6
18204165E7
18204165E8
18204165F0
18204165G0
18204165H0
1820416621
1820416651
1820416681
1820416682
18204166A1
18204166A2
18204166A3
18204166A4
18204166B0
18204166C1
18204166C2
18204166C3

18205286A1
18205286A2
18205286A3
18205286A4
18205286B1
18205286B2
18205286C0
1820528711
1820528741
1820528744
1820528745
1820528751
1820528752
1820528754
1820528782
1820528783
18205287A1
18205287A2
18205287A3
18205287B0
18205287C1
18205287C2
18205287C3
18205287D1
18205287D2
1820528821
1820528831
1820528832
1820528841
1820528842
1820528843
1820528844
1820528845
1820528846
1820528851
1820528852
1820528853
1820528854
1820528855
1820528856
1820528881
1820528882
1820528883
1820528891
18205288A1
18205288A2
18205288A3
18205288A4
18205288B1
18205288B2
18205288B3
18205288B4
18205288C1
18205288C2
18205288C3
1820528911
1820528912
1820528913
1820528914
1820528915
1820528916
1820528917
1820528918
1820528919
18205289110
1820528931
1820528941
1820528942
1820528951
1820528981
1820528982
1820528983
1820528984
1820528991
18205289A1
18205289A2
18205289A3
18205289B1
18205289B2
18205289B3
18205289C0
18205289D1
18205289D2
18205289D3
18205289E1
18205289E2
18205289E3
18205289K1
18205289K2
1820529031
182052904

1820843985
18208439813
18208439A0
18208439B0
18208439D0
1820844031
1820844051
1820844052
1820844053
1820844056
1820844057
1820844082
1820844083
18208440A1
18208440A2
18208440A3
18208440A4
18208440A5
18208440B2
18208440C1
18208440C2
18208440C3
1820844131
1820844132
1820844133
1820844134
1820844135
1820844136
1820844137
1820844138
1820844139
18208441310
18208441311
18208441312
18208441313
18208441314
18208441315
1820844141
1820844142
1820844143
1820844144
1820844145
1820844146
1820844151
1820844152
1820844153
1820844182
1820844183
1820844184
1820844185
1820844186
1820844187
1820844188
1820844189
18208441810
18208441811
18208441812
18208441813
18208441A1
18208441A2
18208441A3
18208441A4
18208441A5
18208441A6
18208441B1
18208441B2
18208441C0
18208441D0
18208441E1
18208441E2
18208441E3
18208441E4
18208441F0
18208441G0
18208441H1
18208441H2
18208441H3
18208441H4
18208441H5
18208441H6
18208441I1
18208441I2
18208441I3
18208441I4
18208441I5
1820844232
1820844284
1820844531
1820844541
1820844542

17701239D4
17701239D5
17701239E0
1770124031
17701240A0
17701240B1
17701240B2
17701240B3
17701240B4
1770124131
1770124132
1770124133
1770124151
17701241A1
17701241A2
17701241A3
17701241A4
17701241B1
17701241B2
17701241B3
17701241B4
17701241B5
17701241C1
17701241C2
17701241C3
17701241C4
17701241C5
17701241C6
17701241D1
17701241D2
17701241D3
17701241E1
17701241E2
17701241F1
17701241F2
17701241F3
17701241F4
17701241F5
17701241G0
1770124231
1770124232
17701242A1
17701242A2
17701242A3
17701242A4
17701242A5
17701242A6
17701242B1
17701242B2
17701242B3
17701242B4
17701242B5
17701242C1
17701242C2
17701242C3
17701242D1
17701242D2
17701242D3
1770124331
1770124332
1770124333
1770124334
1770124381
17701243C0
17701243D1
17701243D2
17701243D3
17701243D4
17701243I0
17701243K0
17701243L0
17701243N0
1770124431
1770124432
1770124433
1770124434
1770124451
1770124461
1770124471
1770124481
17701244A0
17701244B1
17701244B2
17701244B3
17701244B4
17701244B5
17701244B6
17701244H0
17701244L1
17701244L2
17701244M0

17702116D1
17702116D2
17702116D3
17702116D4
17702116D5
17702116E0
17702116F1
17702116F2
17702116F3
17702116F4
17702116G1
17702116G2
17702116G3
17702116H1
17702116H2
17702116H3
17702116H4
1770211781
17702117A1
17702117A2
17702117B1
17702117B2
17702117C0
17702117D0
17702117E0
17702117F0
1770211821
1770211822
1770211823
1770211883
17702118A1
17702118A2
17702118B1
17702118B2
17702118B3
17702118B4
17702118C1
17702118C2
17702118D0
17702118E0
17702118F1
17702118F2
17702118F3
17702118F4
17702118G1
17702118G2
17702118H0
17702118I0
17702118K0
1770211981
17702119A0
17702119B1
17702119B2
17702119B3
17702119B4
17702119C1
17702119C2
17702119C3
17702119D0
17702119F0
17702119G0
1770212021
1770212041
1770212081
17702120A1
17702120A2
17702120A3
17702120A4
17702120A5
17702120A6
17702120B1
17702120B2
17702120B3
17702120C0
17702120D0
17702120F1
17702120F2
1770212141
1770212181
1770212182
1770212183
17702121A0
17702121D1
17702121D2
17702121D3
17702121F1
17702121F2
17702121G0
1770212282
1770212283
1770212284

In [40]:
sap_nutz[sap_nutz['WO']=='17101506C1']

cut_year          WO  cut_volume
0          2007  17101506C1        7.80
121056     2013  17101506C1       14.30
196969     2017  17101506C1        9.75

In [66]:
sap_nutz[(sap_nutz['WO']=='17101506C1') & (sap_nutz['cut_year'] >= fe_year) & (sap_nutz['cut_year'] < flug_year)]

cut_year          WO  cut_volume
121056      2013  17101506C1       14.30
196969      2017  17101506C1        9.75

In [60]:
sap_nutz[sap_nutz['cut_year'] >= fe_year]

cut_year          WO  cut_volume
44044       2009  17101506A0      13.000
44045       2009  17101506G1       2.600
44046       2009  17101507B1       3.250
44047       2009  17101508D1     184.190
44048       2009  17101511C0       3.000
...          ...         ...         ...
259961      2019  18209366H1      29.400
259962      2019  18209366H2       2.950
259963      2019  18209367F1      27.103
259964      2019  18209367K1      37.585
259965      2019  18209368A1     224.048

[215922 rows x 3 columns]